# Tratamiento EMG

In [2]:
import biosignalsnotebooks as bsnb
import numpy as np
import matplotlib.pyplot as plt
import bokeh as bk

## Cargar y mostrar datos

In [3]:
array = np.genfromtxt("./signal_emg.txt", delimiter="\t",skip_header = 3)
Fs = 1000
Ts = 1/Fs
y_raw = array[: ,-2]
time = bsnb.generate_time(y_raw, Fs)

bokeh_fig = bsnb.figure(x_axis_label="Tiempo(s)", y_axis_label="Amplitud")
bokeh_fig.line(time, y_raw, legend_label="EMG data")
bsnb.show(bokeh_fig)


## Filtrar señal

Las señales EMG se suelen filtrar en el rango de 2-500 Hz, ya que se identifican como frecuencias relevantes en la actividad muscular


[1]	L. Gila, A. Malanda, I. Rodríguez Carreño, J. Rodríguez Falces, y J. Navallas, “Métodos de procesamiento y análisis de señales electromiográficas”, An. Sist. Sanit. Navar., vol. 32, pp. 27–43, 2009.

In [5]:
from scipy.signal import butter, lfilter
from scipy.stats import linregress
# eliminar linea de base
y_raw = y_raw - np.mean(y_raw)
y = y_raw - np.mean(y_raw)
# filtrado
low_c = 2
high_c = 450
y = bsnb.aux_functions._butter_bandpass_filter(y, low_c, high_c, Fs)
bokeh_fig = bsnb.figure(x_axis_label="Tiempo(s)", y_axis_label="Amplitud")
bokeh_fig.line(time, y_raw, legend_label="EMG raw")
bokeh_fig.line(time, y, line_color="red", legend_label="EMG filtrado")
bsnb.show(bokeh_fig)


## Detección de eventos

In [6]:
# umbrales
mean_y = np.average(y)
std_y = np.std(y)

t_level1 = 1
t_l = mean_y + t_level1 *std_y
binary_signal = []
for i in range(0, len(time)):
    if y[i] >= t_l:
        binary_signal.append(1)
    else:
        binary_signal.append(0)
binary_signal = np.array(binary_signal)
binary_signal *= int(np.max(y))
bokeh_fig = bsnb.figure(x_axis_label="Tiempo(s)", y_axis_label="Amplitud")
bokeh_fig.line(time, binary_signal,line_color='red', legend_label="binary_signal")
bokeh_fig.line(time, y, legend_label="EMG data")

bsnb.show(bokeh_fig)

In [7]:
burst_begin, burst_end = bsnb.detect_emg_activations(y, Fs, smooth_level=100, threshold_level=2, time_units=True, plot_result=True)[:2]

## Extracción de características

In [8]:
#max
max_samp_val = np.max(y)
#min
min_samp_val = np.min(y)
#rms
rms = np.sqrt(np.sum(y*y))/len(y)

#area
area = np.trapz(y, dx=1/Fs)

time_param = {"Maximum EMG": max_samp_val, "Minimum EMG": min_samp_val,
              "Average EMG": mean_y, "Standard Deviation EMG": std_y, "RMS EMG": rms, "Area EMG": area}
print(time_param)
#señal rectificada
y_rect = np.abs(y)
#media movil
window_size = 500
i = 0
moving_averages = []
while i < len(y_rect) - window_size + 1:
	window_average = round(np.sum(y_rect[i:i+window_size]) / window_size, 2)
	moving_averages.append(window_average)
	i += 1

bokeh_fig = bsnb.figure(x_axis_label="Tiempo(s)", y_axis_label="Amplitud")
bokeh_fig.line(time, moving_averages, legend_label="Media móvil (RMS) de EMG")

bsnb.show(bokeh_fig)


{'Maximum EMG': 409.02915060540397, 'Minimum EMG': -369.05209037276717, 'Average EMG': 0.0002634850608363508, 'Standard Deviation EMG': 22.26555211299467, 'RMS EMG': 0.10099859541111765, 'Area EMG': 0.012597231690838848}


RMS es una herramienta util para suavizar la señal e identificar la activación múscular el nivel de activación.

[2] mdurance, “Guía básica (con ejemplos) para interpretar la electromiografía [+ VIDEO]”, mDurance estudio, 18-ago-2020. [En línea]. Disponible en: https://blog.mdurance.eu/academia/guia-basica-como-interpretar-la-electromiografia/.